In [4]:
## Sep. 09, 2021, train the model for downscale estimation, Xiaole Zhang
from sklearn import linear_model
import pandas as pd
from sklearn.ensemble import BaggingRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import AdaBoostRegressor 
from sklearn.tree import ExtraTreeRegressor
# save https://scikit-learn.org/stable/modules/model_persistence.html
from joblib import dump, load 
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn import preprocessing
import numpy as np

year = 2019
coronaScenrio = 0.1
predictFlag = True
trainFlag = True
withHour = True
allData = False
swissCalc = False # to calculate the map for Switzerland

sitesFlag = False
siteName = "LUG-BAS"
pollutantType = "NO2"

data = pd.read_csv("../data/pollutants/downScale/" +pollutantType+"_trainData.csv")


data = data.convert_objects(convert_numeric=True)

# Replacing infinite with nan
data.replace([np.inf, -np.inf], np.nan, inplace=True)

data = data.dropna()
data.head()

X = data.iloc[:,:-1]
Y = data.iloc[:,-1]


# Y = Y*1000000

if(predictFlag):
    scaler = preprocessing.StandardScaler().fit(X)
    X_train_transformed = scaler.transform(X)
    y_train = Y
    #regressor = ExtraTreeRegressor(random_state=0,max_features=6)

    # cross validation to decide the parameters
    # https://scikit-learn.org/stable/modules/cross_validation.html
    #regr = BaggingRegressor(base_estimator=regressor, n_estimators=300, random_state=0, n_jobs=6)
    #scores = cross_val_score(regr, X_train_transformed, y_train, cv=5)

    if(trainFlag):
    ## https://scikit-learn.org/stable/modules/generated/sklearn.ensemble.BaggingRegressor.html
        #regr = BaggingRegressor(base_estimator=regressor, n_estimators=500, random_state=0, n_jobs=6).fit(X_train_transformed,y_train)
        # regr = ExtraTreesRegressor(n_estimators=600, random_state=0,max_features=4, n_jobs=6).fit(X_train_transformed,y_train)
        
        regr = RandomForestRegressor(n_estimators=100, random_state=0,max_features=4,bootstrap=False, n_jobs=6).fit(X_train_transformed,y_train)
        #regressor = ExtraTreeRegressor(random_state=0,max_features=5)
        #regr =AdaBoostRegressor(base_estimator=regressor,n_estimators=200).fit(X_train_transformed,y_train)
        #dump(regr, 'trainedModel.joblib') 
    else :
        regr = load('trainedModel.joblib') 

    
    if(swissCalc):
        # prediction
        #dataPred = pd.read_csv("pollutants/downScale/predData.csv")
        #dataPred.fillna(0, inplace=True)
        
        for hourId in range(8760):
            print(hourId)
            data = np.fromfile("pollutants/downScale/"+str(year)+"/"+str(hourId)+"_"+pollutantType+"_predData.bin", dtype=np.float32)
            data = np.reshape(data,(-1,112041))
            data = pd.DataFrame(np.transpose(data))
            dataPred = data.convert_objects(convert_numeric=True)
            dataPred.fillna(0, inplace=True)
            
            cams = data.iloc[:, 0]

            XPred = dataPred.iloc[:,:]


            X_pred_transformed = scaler.transform(XPred)
            Y_pred = regr.predict(X_pred_transformed)
            
            pred = np.multiply(cams,Y_pred)

            np.savetxt("pollutants/downScale/"+str(year)+"/"+str(hourId)+"_downScale_"+pollutantType+".csv", pred, delimiter=",")

    else:
        # prediction
        dataPred = pd.read_csv("data/cpcTrainData2020.csv")
        infos = dataPred.iloc[:,:2]
        dataPred = dataPred.iloc[:,2:]

        dataPred = dataPred.convert_objects(convert_numeric=True)
        dataPred = pd.concat([infos, dataPred], axis=1)

        dataPred = dataPred.dropna()
        dataPred = dataPred.reset_index(drop=True)

        XPred = dataPred.iloc[:,2:-1]
        YTrue = dataPred.iloc[:,-1]


        X_pred_transformed = scaler.transform(XPred)
        Y_pred = regr.predict(X_pred_transformed)

        Y_predData = pd.DataFrame(Y_pred, columns=["prediction"])
        dataAll = pd.concat([dataPred, Y_predData], axis=1)

        np.savetxt("prediction_2020_downScale.csv", Y_pred, delimiter=",")
        if(sitesFlag):
            dataAll.to_csv("predictions-without" + siteName + "_downScale.csv")
        else:
            dataAll.to_csv("predictions-all_downScale.csv")
            
else:
    X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.00001, random_state=0)
    scaler = preprocessing.StandardScaler().fit(X_train)
    X_train_transformed = scaler.transform(X_train)
    X_test_transformed = scaler.transform(X_test)
        

    regressor = ExtraTreeRegressor(random_state=0,max_features=5)

    # cross validation to decide the parameters
    # https://scikit-learn.org/stable/modules/cross_validation.html
    # regr = BaggingRegressor(base_estimator=regressor, n_estimators=500,random_state=0, n_jobs=6)
   
    #regr = ExtraTreesRegressor(n_estimators=600, random_state=0,max_features=4, n_jobs=6)
    regr = RandomForestRegressor(n_estimators=100, random_state=0,max_features=4,bootstrap=False, n_jobs=6)
    
    # regr =AdaBoostRegressor(base_estimator=regressor,n_estimators=200)
    scores = cross_val_score(regr, X_train_transformed, y_train, cv=5)


    

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:32: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


0


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:80: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


1


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:80: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


...

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:80: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


8758


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:80: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


8759


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:80: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


In [10]:
pred = numpy.multiply(cams,Y_pred)

NameError: name 'numpy' is not defined

In [14]:
regr.score(X_test_transformed,y_test)

NotFittedError: This RandomForestRegressor instance is not fitted yet. Call 'fit' with appropriate arguments before using this estimator.

In [2]:
regr.score(X_pred_transformed,YTrue)

NameError: name 'X_pred_transformed' is not defined

In [2]:
print("%0.5f accuracy with a standard deviation of %0.5f" % (scores.mean(), scores.std()))

0.80187 accuracy with a standard deviation of 0.00249


In [112]:
dataPred = pd.read_csv("data/cpcTrainData2020.csv")
infos = dataPred.iloc[:,:2]
dataPred = dataPred.iloc[:,2:]

In [8]:
X_train[X_train.isnull().any(axis=1)]

Empty DataFrame
Columns: [gre000h0, tre200h0, rre150h0, ure200h0, fkl010h0, O3_ug_m3_, NO2_ug_m3_, PM2_5_ug_m3_, PM10_ug_m3_, NOX_ug_m3Eq_NO2_]
Index: []

In [3]:
siteName = 'te'
"data/cpcTrainData-without" + str(year) + ".csv"

'data/cpcTrainData-without2020.csv'

In [1]:
"swissPNC/prediction_"+str(year)+".csv"


NameError: name 'year' is not defined